In [1]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore') 

In [1]:
#from google.colab import drive
#drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [4]:
!pip install flask-ngrok

In [5]:
!pip install transformers

In [2]:
import glob
from tqdm import tqdm
import matplotlib.pyplot as plt
from wordcloud import WordCloud 
from pythainlp.corpus import thai_stopwords
from pythainlp.tokenize import word_tokenize # ใช้ในการตัดคำ

In [3]:
!pip install stop_words

In [6]:
!pip install wordcloud pyicu

    ERROR: Command errored out with exit status 1:
     command: 'C:\Users\LENOVO\miniconda3\python.exe' -c 'import sys, setuptools, tokenize; sys.argv[0] = '"'"'C:\\Users\\LENOVO\\AppData\\Local\\Temp\\pip-install-upwdje_8\\pyicu\\setup.py'"'"'; __file__='"'"'C:\\Users\\LENOVO\\AppData\\Local\\Temp\\pip-install-upwdje_8\\pyicu\\setup.py'"'"';f=getattr(tokenize, '"'"'open'"'"', open)(__file__);code=f.read().replace('"'"'\r\n'"'"', '"'"'\n'"'"');f.close();exec(compile(code, __file__, '"'"'exec'"'"'))' egg_info --egg-base 'C:\Users\LENOVO\AppData\Local\Temp\pip-install-upwdje_8\pyicu\pip-egg-info'
         cwd: C:\Users\LENOVO\AppData\Local\Temp\pip-install-upwdje_8\pyicu\
    Complete output (53 lines):
    Traceback (most recent call last):
      File "C:\Users\LENOVO\AppData\Local\Temp\pip-install-upwdje_8\pyicu\setup.py", line 63, in <module>
        ICU_VERSION = os.environ['ICU_VERSION']
      File "C:\Users\LENOVO\miniconda3\lib\os.py", line 675, in __getitem__
        raise KeyEr

In [3]:
import pythainlp
from pythainlp.corpus import thai_stopwords
from pythainlp.corpus import wordnet
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words

In [4]:
import nltk
nltk.download('words')
th_stop = ' '.join(list(thai_stopwords()))
#th_stop = tuple(thai_stopwords('thai'))
en_stop = tuple(get_stop_words('en'))
p_stemmer = PorterStemmer()

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\LENOVO\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


In [6]:
#!pip install tensorflow-gpu==1.15

In [5]:
import tensorflow as tf
print(tf.__version__)

2.3.0


In [2]:
!pip install pythainlp

In [6]:
from flask import Flask, jsonify, request
from flask_ngrok import run_with_ngrok
from transformers import AutoTokenizer, AutoModel
from transformers import BertTokenizer
from pythainlp.tokenize import word_tokenize
#from google.colab import widgets
import numpy as np
import json
from numpy import load
import pandas as pd

In [7]:
app = Flask(__name__)
run_with_ngrok(app)

In [8]:
pretrained = "monsoon-nlp/bert-base-thai"#@param ["monsoon-nlp/bert-base-thai"] 

In [9]:
#model_path = '/content/drive/MyDrive/LegalBERT/model_finetuning/save_model/1611409445'
model_path = 'C:\\Users\\LENOVO\\Desktop\\Webapp_LegalBERTth\\model_finetuning\\save_model\\1611409445'

In [10]:
session_config = tf.compat.v1.ConfigProto(allow_soft_placement=True)
session_config.gpu_options.allow_growth = True
sess = tf.compat.v1.Session(config=session_config)
tf.compat.v1.saved_model.loader.load(sess, [tf.compat.v1.saved_model.tag_constants.SERVING], model_path)

Instructions for updating:
This function will only be available through the v1 compatibility library as tf.compat.v1.saved_model.loader.load or tf.compat.v1.saved_model.load. There will be a new function for importing SavedModels in Tensorflow 2.0.
INFO:tensorflow:Restoring parameters from C:\Users\LENOVO\Desktop\Webapp_LegalBERTth\model_finetuning\save_model\1611409445\variables\variables


meta_info_def {
  stripped_op_list {
    op {
      name: "Add"
      input_arg {
        name: "x"
        type_attr: "T"
      }
      input_arg {
        name: "y"
        type_attr: "T"
      }
      output_arg {
        name: "z"
        type_attr: "T"
      }
      attr {
        name: "T"
        type: "type"
        allowed_values {
          list {
            type: DT_BFLOAT16
            type: DT_HALF
            type: DT_FLOAT
            type: DT_DOUBLE
            type: DT_UINT8
            type: DT_INT8
            type: DT_INT16
            type: DT_INT32
            type: DT_INT64
            type: DT_COMPLEX64
            type: DT_COMPLEX128
            type: DT_STRING
          }
        }
      }
    }
    op {
      name: "AddV2"
      input_arg {
        name: "x"
        type_attr: "T"
      }
      input_arg {
        name: "y"
        type_attr: "T"
      }
      output_arg {
        name: "z"
        type_attr: "T"
      }
      attr {
        name: "T"
      

In [11]:
name = pretrained
#tokenizer = AutoTokenizer.from_pretrained(name)
#model = AutoModel.from_pretrained(name)
tz = BertTokenizer.from_pretrained(name)

In [12]:
#Data Proprocessing before prediction
def split_word(text):
     
    tokens = word_tokenize(text, engine="newmm")
    
    # Remove stop words ภาษาไทย และภาษาอังกฤษ
    tokens = [i for i in tokens if not i in th_stop and not i in en_stop]
    
    # หารากศัพท์ภาษาไทย และภาษาอังกฤษ
    # English
    tokens = [p_stemmer.stem(i) for i in tokens]
    
    # Thai
    tokens_temp=[]
    for i in tokens:
        w_syn = wordnet.synsets(i)
        if (len(w_syn)>0) and (len(w_syn[0].lemma_names('tha'))>0):
            tokens_temp.append(w_syn[0].lemma_names('tha')[0])
        else:
            tokens_temp.append(i)
    
    tokens = tokens_temp
    
    # ลบตัวเลข
    tokens = [i for i in tokens if not i.isnumeric()]
    
    # ลบช่องว่าง
    tokens = [i for i in tokens if not ' ' in i]

    return tokens

In [13]:
def predict_text(input_value):
    #ตัดคำ
    e=split_word(input_value) 

    #Extrac Feature input for Prediction
    #tz = BertTokenizer.from_pretrained(name)
    # The senetence to be encoded
    # Encode the sentence
    encoded = tz.encode_plus(
        text=e,  # the sentence to be encoded
        add_special_tokens=True,  # Add [CLS] and [SEP]
        max_length = 128,  # maximum length of a sentence
        pad_to_max_length=True,  # Add [PAD]s
        return_attention_mask = True,  # Generate the attention mask
        return_tensors = 'pt',  # ask the function to return PyTorch tensors
)
        # Get the input IDs and attention mask in tensor format
    input_ids = encoded['input_ids']
    input_ids_new = np.array((input_ids),dtype = 'int64')

    softmax_tensor = sess.graph.get_tensor_by_name('loss/Softmax:0')
    predictions = sess.run(softmax_tensor, {'Placeholder:0': input_ids_new})

    labels = np.array([['Personal Rights', 'family', 'labor', 'contract', 'criminal']])
    for i in range(predictions.shape[1]):
        score = predictions.max()
        if predictions[0,i] == score :
            tag = labels[0,i]
            tag = str(tag)
    
    print(predictions)
    print((score*100))
    return tag, input_ids_new

#  function Feature vector

#### Numpy Broadcast to perform euclidean distance vectorized

In [14]:
#function euclidean distance
def EuclideanDistance(input_ids_new, all_fea):
    Distance = np.sqrt((np.square(input_ids_new[:,np.newaxis]-all_fea).sum(axis=2)))
    #numpy.ndarray to list
    list_Distance = Distance.tolist()
    list_Distance_2 =[x for xs in list_Distance for x in xs] 
    
    return list_Distance_2 #return list of number edu distance

In [15]:
#Function create Dataframe
def create_table(list_question, list_anws, list_dist):
    #tag_data = Data.loc[Data['tag'] == 'กฎหมายอาญา(Criminal)'].reset_index(drop=True)
    #message_list = tag_table['message'].to_list()
    tabel_feature = pd.DataFrame(list(zip(list_question,list_anws, list_dist)), 
                      columns =['question', 'answer', 'distance'])
    
    return tabel_feature

In [16]:
def create_df_similarity(tabel_feature):
    tabel_feature_sort = tabel_feature.sort_values(by=['distance']).reset_index(drop=True)
    similarity_rank3 = tabel_feature_sort[0:3]
    question_similarity_rank3 = similarity_rank3['question']
    anws_similarity_rank3 = similarity_rank3['answer']
    question_similar1 = question_similarity_rank3[0] 
    anws_similar1 = anws_similarity_rank3[0] 
    question_similar2 = question_similarity_rank3[1] 
    anws_similar2 = anws_similarity_rank3[1]
    question_similar3 = question_similarity_rank3[2]
    anws_similar3 = anws_similarity_rank3[2]
    
    return question_similar1, anws_similar1, question_similar2, anws_similar2, question_similar3, anws_similar3

In [17]:
#function หลัก
#function display rank3 Q&A Similarity
def text_similarity(tag_law, input_ids_new):
    #'%s' % tag_law 
    #read feature file
    feature_all_tag = np.load("%s.npy" % tag_law) 
    #calculate Distance
    list_dist = EuclideanDistance(input_ids_new, feature_all_tag)
    #create dataframe
    df = pd.read_csv('%s.csv' % tag_law)    
    list_question = df['คำถาม'].to_list()
    list_anws = df['คำตอบ'].to_list()
    tabel_feature = create_table(list_question, list_anws, list_dist)
    #sort Euclidean distance
    question_similar1, anws_similar1, question_similar2, anws_similar2, question_similar3, anws_similar3 = create_df_similarity(tabel_feature)
        
    return question_similar1, anws_similar1, question_similar2, anws_similar2, question_similar3, anws_similar3    

In [2]:
#question_similar1, anws_similar1, question_similar2, anws_similar2, question_similar3, anws_similar3 = text_similarity(tag, input_ids_new)

In [18]:
@app.route("/predict", methods=["POST"])
def predict():
    #result = []
  #result_text1 = 0
  #result_text2 = 0
  #result_text3 = 0
    if request.method == "POST":
        input_value = request.form["text"]
        tag_law, input_ids_new = predict_text(input_value)
        question_similar1, anws_similar1, question_similar2, anws_similar2, question_similar3, anws_similar3 = text_similarity(tag_law, input_ids_new)
    ##ดึงคำตอบมาด้วย
    # ประมวลผล #
        print(input_value)
        print(tag_law)
        print(question_similar1)
        print(anws_similar1)
        print(question_similar2)
        print(anws_similar2)
        print(question_similar3)
        print(anws_similar3)

        json_data = json.dumps({'input_text':input_value, 'result_tag':tag_law, 'result_Q1':question_similar1, 'result_A1':anws_similar1, 'result_Q2':question_similar2, 'result_A2':anws_similar2, 'result_Q3':question_similar3, 'result_A3':anws_similar3})
        #results.append(json_data)
        
    return json_data

In [ ]:
if __name__ == '__main__':
    app.run()

 * Running on http://127.0.0.1:5000/ (Press CTRL+C to quit)


 * Running on http://df41becabdc4.ngrok.io
 * Traffic stats available on http://127.0.0.1:4040


Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
127.0.0.1 - - [12/Mar/2021 21:50:15] "POST /predict HTTP/1.1" 200 -


[[3.9405527e-04 9.9714249e-01 3.5907893e-04 1.0416972e-03 1.0627374e-03]]
99.7142493724823
สามีไปแต่งงานกับหญิงอีกคน ทั้งที่เรากับสามียังจดทะเบียนสมรสกันอยู่ สามารถฟ้องหญิงคนนั้นได้ไหม
family
สามีมีความสัมพันธ์กับหญิงอืนจนกระทั่งไปแต่งงานกันเราจะฟ้องหญิงคนนั้นได้หรือไม่
การที่สามีไปมีความสัมพันธ์กับหญิงอื่นนั้นหากจะเป็นการฟ้องก็ต้องฟ้องเรียกค่าทดแทนเพราะเหตุหญิงอื่นแสดงตนโดยเปิดเผยว่าตนมีความสัมพันธ์กับสามีในทำนองชู้สาวซึ่งมีกฎหมายที่เกี่ยวข้องคือประมวลกฎหมายแพ่งและพาณิชน์มาตรามาตราโดยในวรรคสองบัญญัติว่าสามีจะเรียกค่าทดแทนจากผู้ซึ่งล่วงเกินภริยาไปในทำนองชู้สาวก็ได้และภริยาจะเรียกค่าทดแทนจากหญิงอื่นที่แสดงตนโดยเปิดเผยเพื่อแสดงว่าตนมีความสัมพันธ์กับสามีในทำนองชู้สาวก็ได้นั่นก็หมายความว่าเราสามารถเรียกค่าทดแทนตามสิทธิที่กฎหมายเปิดช่องให้ได้โดยนำคดีไปฟ้องยังศาลเยาวชนและครอบครัวทั้งนี้การเป็นสามีภรรยากันนั้นต้องเป็นสามีภรรยากันโดยชอบด้วยกฎหมายนะซึ่งกรณีลักษณะนี้มีแนวคำพิพากษาฏีกาอยู่หลายเรื่องเช่นคำพิพากษาศาลฎีกาที่ทั้งนี้หากจะดำเนินคดีก็จะต้องจัดเตรียมหลักฐานและเอกสารต่างๆให้พร้อมทั้งพยานบ

127.0.0.1 - - [12/Mar/2021 21:50:31] "POST /predict HTTP/1.1" 200 -


...

[[4.6447062e-04 9.9265265e-01 2.3616890e-03 3.6434301e-03 8.7772874e-04]]
99.26526546478271
มีการทำยอมไว้กับโจทก์แต่เสียชีวิตก่อนที่จะชำระแบบนี้สามารถให้ทายาทที่ถูกต้องตามกฎหมายชำระค่าทำยอมแทนได้หรือไม่
family
ลูกอายุปีจะเปลี่ยนนามสกุลใหม่โดยที่พ่อแม่ก็ยังใช้นามสกุลเดิมจะสามารถทำได้รึป่าว
สามารถกระทำได้เพราะบุตรมีอายุที่บรรลุนิติภาวะแล้วโดยยื่นคำร้องต่อนายทะเบียนเพื่อขอเปลี่ยนชื่อสกุลตามที่กฎหมายว่าด้วยการนั้นกำหนดไว้
ผู้เยาว์อายุสามารถซื้อบ้านได้หรือไม่ถ้ามีผู้ปกครองให้ความยินยอม
ผู้เยาว์อาจทำการใดๆได้ทั้งสิ้นหากเป็นเพียงเพื่อจะได้ไปซึ่งสิทธิอันใดอันหนึ่งดังนั้นการทำนิติกรรมซื้อบ้านจึงเป็นการทำนิติกรรมได้ไปซึ่งกรรมสิทธิ์แห่งบ้านที่ซื้อย่อมไม่จำต้องให้บิดามารดาซึ่งเป็นผู้แทนโดยชอบธรรมให้ความยินยอมด้วยแต่อย่างใดแต่หากบิดามารดาหรือผู้ปกครองให้ความยินยอมด้วยก็เป็นเรื่องที่ดีสามารถกระทำได้
ผู้เป็นย่าสามารถโอนบ้านพร้อมที่ดินให้กับหลานที่มีอายุขวบได้หรือไม่
สามารถทำได้เพราะเป็นการรับให้โดยเสน่หาตามประมวลกฎหมายแพ่งและพาณิชย์มาตรา๑๕๗๔๙


127.0.0.1 - - [12/Mar/2021 22:19:07] "POST /predict HTTP/1.1" 200 -


[[4.6447062e-04 9.9265265e-01 2.3616890e-03 3.6434301e-03 8.7772874e-04]]
99.26526546478271
มีการทำยอมไว้กับโจทก์แต่เสียชีวิตก่อนที่จะชำระแบบนี้สามารถให้ทายาทที่ถูกต้องตามกฎหมายชำระค่าทำยอมแทนได้หรือไม่
family
ลูกอายุปีจะเปลี่ยนนามสกุลใหม่โดยที่พ่อแม่ก็ยังใช้นามสกุลเดิมจะสามารถทำได้รึป่าว
สามารถกระทำได้เพราะบุตรมีอายุที่บรรลุนิติภาวะแล้วโดยยื่นคำร้องต่อนายทะเบียนเพื่อขอเปลี่ยนชื่อสกุลตามที่กฎหมายว่าด้วยการนั้นกำหนดไว้
ผู้เยาว์อายุสามารถซื้อบ้านได้หรือไม่ถ้ามีผู้ปกครองให้ความยินยอม
ผู้เยาว์อาจทำการใดๆได้ทั้งสิ้นหากเป็นเพียงเพื่อจะได้ไปซึ่งสิทธิอันใดอันหนึ่งดังนั้นการทำนิติกรรมซื้อบ้านจึงเป็นการทำนิติกรรมได้ไปซึ่งกรรมสิทธิ์แห่งบ้านที่ซื้อย่อมไม่จำต้องให้บิดามารดาซึ่งเป็นผู้แทนโดยชอบธรรมให้ความยินยอมด้วยแต่อย่างใดแต่หากบิดามารดาหรือผู้ปกครองให้ความยินยอมด้วยก็เป็นเรื่องที่ดีสามารถกระทำได้
ผู้เป็นย่าสามารถโอนบ้านพร้อมที่ดินให้กับหลานที่มีอายุขวบได้หรือไม่
สามารถทำได้เพราะเป็นการรับให้โดยเสน่หาตามประมวลกฎหมายแพ่งและพาณิชย์มาตรา๑๕๗๔๙


127.0.0.1 - - [12/Mar/2021 22:19:52] "POST /predict HTTP/1.1" 200 -


[[4.2526665e-04 9.9513799e-01 1.2706572e-03 2.4934313e-03 6.7266973e-04]]
99.51379895210266
มีการทำยอมไว้กับโจทก์แต่เสียชีวิตก่อนที่จะชำระแบบนี้สามารถให้ทายาทที่ถูกต้องตามกฎหมายชำระค่าทำยอมแทนได้หรือไม่ เพราะเหตุใด
family
ลูกอายุปีจะเปลี่ยนนามสกุลใหม่โดยที่พ่อแม่ก็ยังใช้นามสกุลเดิมจะสามารถทำได้รึป่าว
สามารถกระทำได้เพราะบุตรมีอายุที่บรรลุนิติภาวะแล้วโดยยื่นคำร้องต่อนายทะเบียนเพื่อขอเปลี่ยนชื่อสกุลตามที่กฎหมายว่าด้วยการนั้นกำหนดไว้
ผู้เยาว์อายุสามารถซื้อบ้านได้หรือไม่ถ้ามีผู้ปกครองให้ความยินยอม
ผู้เยาว์อาจทำการใดๆได้ทั้งสิ้นหากเป็นเพียงเพื่อจะได้ไปซึ่งสิทธิอันใดอันหนึ่งดังนั้นการทำนิติกรรมซื้อบ้านจึงเป็นการทำนิติกรรมได้ไปซึ่งกรรมสิทธิ์แห่งบ้านที่ซื้อย่อมไม่จำต้องให้บิดามารดาซึ่งเป็นผู้แทนโดยชอบธรรมให้ความยินยอมด้วยแต่อย่างใดแต่หากบิดามารดาหรือผู้ปกครองให้ความยินยอมด้วยก็เป็นเรื่องที่ดีสามารถกระทำได้
ผู้เป็นย่าสามารถโอนบ้านพร้อมที่ดินให้กับหลานที่มีอายุขวบได้หรือไม่
สามารถทำได้เพราะเป็นการรับให้โดยเสน่หาตามประมวลกฎหมายแพ่งและพาณิชย์มาตรา๑๕๗๔๙
